In [1]:
import numpy as np
import pandas as pd
import json
import collections
from collections import defaultdict 
from functools import partial
import networkx as nx
import matplotlib.pyplot as plt
import seaborn as sns
from tqdm import tqdm

import jax

# Global flag to set a specific platform, must be used at startup.
jax.config.update('jax_platform_name', 'gpu')
jax.config.update("jax_debug_nans", True)
jax.config.update("jax_debug_infs", True)

jax.config.update('jax_log_compiles', False)
jax.config.update('jax_check_tracer_leaks', False)

In [2]:
# Good read: https://iq-inc.com/importerror-attempted-relative-import/

import sys
import importlib
from mimicnet import concept
from mimicnet import jax_interface
from mimicnet import dag
from mimicnet import glove
from mimicnet import gram
from mimicnet import ode

importlib.reload(sys.modules['mimicnet.concept'])
importlib.reload(sys.modules['mimicnet.dag'])
importlib.reload(sys.modules['mimicnet.jax_interface'])
importlib.reload(sys.modules['mimicnet.glove'])
importlib.reload(sys.modules['mimicnet.gram'])
importlib.reload(sys.modules['mimicnet.ode'])

/home/asem/.conda/envs/mimic3-snonet/lib/python3.9/site-packages/jax/experimental/optimizers.py:28: FutureWarning: jax.experimental.optimizers is deprecated, import jax.example_libraries.optimizers instead
  warnings.warn('jax.experimental.optimizers is deprecated, '


<module 'mimicnet.ode' from '/home/asem/GP/MIMIC-SNONET/mimicnet/ode.py'>

In [3]:

KG = dag.CCSDAG()

In [4]:
# multi_visit_mimic_dir = '/home/am8520/GP/ehr-data/mimic3-multi-visit'
multi_visit_mimic_dir = '/home/asem/GP/ehr-data/mimic3-multi-visit'
transformed_mimic_dir = '/home/asem/GP/ehr-data/mimic3-transforms'
mimic_dir = '/home/asem/GP/ehr-data/mimic3-v1.4/physionet.org/files/mimiciii/1.4'
experiments_dir = '/home/asem/GP/ehr-data/mimic3-snonet-exp'
experiment_prefix = 'NOV29'

In [5]:
D_LABITEMS = pd.read_csv(f'{mimic_dir}/D_LABITEMS.csv.gz')
D_ITEMS = pd.read_csv(f'{mimic_dir}/D_ITEMS.csv.gz')
D_TEST = pd.concat([D_LABITEMS, D_ITEMS], join='inner')
test_label_dict = dict(zip(D_TEST.ITEMID, D_TEST.LABEL))
test_cat_dict = dict(zip(D_TEST.ITEMID, D_TEST.CATEGORY))

In [6]:
static_df = pd.read_csv(f'{transformed_mimic_dir}/static_df.csv.gz')
adm_df = pd.read_csv(f'{transformed_mimic_dir}/adm_df.csv.gz')
diag_df = pd.read_csv(f'{transformed_mimic_dir}/diag_df.csv.gz', dtype={'ICD9_CODE': str})
proc_df = pd.read_csv(f'{transformed_mimic_dir}/proc_df.csv.gz', dtype={'ICD9_CODE': str})
test_df = pd.read_csv(f'{transformed_mimic_dir}/test_df.csv.gz')


In [7]:
# Cast columns of dates to datetime64

static_df['DOB'] = pd.to_datetime(static_df.DOB, infer_datetime_format=True).dt.normalize()
adm_df['ADMITTIME'] = pd.to_datetime(adm_df.ADMITTIME, infer_datetime_format=True).dt.normalize()
adm_df['DISCHTIME'] = pd.to_datetime(adm_df.DISCHTIME, infer_datetime_format=True).dt.normalize()
test_df['DATE'] = pd.to_datetime(test_df.DATE, infer_datetime_format=True).dt.normalize()

In [8]:
static_df.ETHNIC_GROUP.nunique()

7

In [9]:
test_df

SUBJECT_ID  ITEMID       DATE     VALUE
0                17   50852 2134-12-22 -1.201339
1                17   50861 2134-12-22 -0.809370
2                17   50862 2134-12-22  1.634410
3                17   50863 2134-12-22 -1.452596
4                17   50867 2134-12-22 -0.608894
...             ...     ...        ...       ...
4546204       99982  227456 2157-02-22  1.794272
4546205       99982  227457 2157-02-22 -0.723781
4546206       99982  227465 2157-02-22  2.247434
4546207       99982  227466 2157-02-22 -0.029395
4546208       99982  227467 2157-02-22  2.186595

[4546209 rows x 4 columns]

In [10]:
patients = concept.Subject.to_list(static_df, adm_df, diag_df, proc_df, test_df)

In [11]:
len(patients)

4434

In [12]:
# ehr_dfs = concept.Subject.to_df(patients)

In [13]:
# def df_eq(df1, df2):
#     df11 = df1.sort_values(by=df1.columns.tolist()).reset_index(drop=True)
#     df22 = df2.sort_values(by=df2.columns.tolist()).reset_index(drop=True)
#     return df11[df22.columns].equals(df22)

# all(map(df_eq, ehr_dfs, [static_df, adm_df, diag_df, proc_df, test_df]))

### [FORK] Skip the cell below to load the jaxified data from a stored file on disc

In [14]:
# subjects_interface = jax_interface.SubjectJAXInterface(patients, set(test_df.ITEMID), KG)
# import pickle
# with open(f'{experiments_dir}/{experiment_prefix}_subjects_interface.pkl', 'wb') as pickleFile:
#     pickle.dump(subjects_interface, pickleFile)

In [15]:
import pickle
with open(f'{experiments_dir}/{experiment_prefix}_subjects_interface.pkl', 'rb') as pickleFile:
    subjects_interface = pickle.load(pickleFile)

## GloVe Initialization

In [16]:
%load_ext autoreload
%autoreload 2

In [17]:
import logging
logging.basicConfig(level=logging.DEBUG)
logging.debug("test")

DEBUG:root:test


In [18]:
glove_args = {
    'diag_idx': subjects_interface.diag_multi_ccs_idx,
    'proc_idx': subjects_interface.proc_multi_ccs_idx,
    'ccs_dag': KG,
    'subjects': patients,
    'diag_vector_size': 100,
    'proc_vector_size': 60,
    'iterations': 30,
    'window_size_days': 2 * 365
}

diag_glove_rep, proc_glove_rep = glove.glove_representation(**glove_args)

In [19]:
print(f'#point_indices: {len(subjects_interface.nth_points)}')
print(f'#total_points: {sum(len(points) for n, points in subjects_interface.nth_points.items())}')

#[len(points) for n, points in subjects_interface.nth_points.items()]

#point_indices: 1085
#total_points: 129334


## GRAM objects

In [20]:
from datetime import datetime
daily_tracer = "/tmp/tensorboard/"+ datetime.now().strftime("%Y%m%d-%H%M%S") 
print(daily_tracer)

/tmp/tensorboard/20211201-133353


In [21]:


logs = '/tmp/tensorboard/20210708-182059'
#server = jax.profiler.start_server(9999)

In [22]:
       
config = {
    'gram_config': {
        'diag': {
            'ccs_dag': KG,
            'code2index': subjects_interface.diag_multi_ccs_idx,
            'attention_method': 'tanh', #l2, tanh
            'attention_dim': 100,
            'ancestors_mat': subjects_interface.diag_multi_ccs_ancestors_mat,
            'basic_embeddings': diag_glove_rep
        },
        'proc': {
            'ccs_dag': KG,
            'code2index': subjects_interface.proc_multi_ccs_idx,
            'attention_method': 'tanh',
            'attention_dim': 60,
            'ancestors_mat': subjects_interface.proc_multi_ccs_ancestors_mat,
            'basic_embeddings': proc_glove_rep
        }
    },
    'model': {
        'ode_dyn': 'mlp', # gru, mlp
        'state_size': 50,
        'numeric_hidden_size': 40,
        'bias': True
    },
    'training': {
        'train_validation_split': 0.8,
        'batch_size': 8,
        'epochs': 1,
        'lr': 1e-3,
        'diag_loss': 'balanced_focal', # balanced_focal, bce
        'tay_reg': None, # Order of regularized derivative of the dynamics function (None for disable).
        'loss_mixing': {
            'num_alpha': 0.1,
            'diag_alpha': 0.1,
            'ode_alpha': 1e-3,
            'l1_reg': 1e-6,
            'l2_reg': 1e-5,
            'dyn_reg': 1e-5
        },
        'eval_freq': 1,
        'save_freq': 100,
        'save_params_prefix': None
    }
}


In [23]:
diag_gram = gram.DAGGRAM(**config['gram_config']['diag'])

DEBUG:absl:Initializing backend 'interpreter'
DEBUG:absl:Backend 'interpreter' initialized
DEBUG:absl:Initializing backend 'cpu'
DEBUG:absl:Backend 'cpu' initialized
DEBUG:absl:Initializing backend 'tpu_driver'
INFO:absl:Unable to initialize backend 'tpu_driver': NOT_FOUND: Unable to find driver in registry given worker: 
DEBUG:absl:Initializing backend 'gpu'
INFO:absl:Unable to initialize backend 'gpu': NOT_FOUND: Could not find registered platform with name: "cuda". Available platform names are: Interpreter Host
DEBUG:absl:Initializing backend 'tpu'
INFO:absl:Unable to initialize backend 'tpu': INVALID_ARGUMENT: TpuPlatform is not available.
DEBUG:absl:Compiling atleast_2d (140237611332032) for args (ShapedArray(float32[100]),).
DEBUG:absl:Compiling prim_fun (140237611453440) for args (ShapedArray(float32[1,100]), ShapedArray(float32[1,100]), ShapedArray(float32[1,100]), ShapedArray(float32[1,100]), ShapedArray(float32[1,100]), ShapedArray(float32[1,100]), ShapedArray(float32[1,100])

In [24]:
proc_gram = gram.DAGGRAM(**config['gram_config']['proc'])

DEBUG:absl:Compiling atleast_2d (140237611376960) for args (ShapedArray(float32[60]),).
DEBUG:absl:Compiling prim_fun (140237611376960) for args (ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60])).
DEBUG:absl:Compiling prim_fun (140237611422912) for args (ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60]), ShapedArray(float32[1,60])).
DEBUG:absl:Compiling prim_fun (140237611344576) for args (ShapedArray(float32[16,60]), ShapedA

## GRU-ODE-Bayes

In [25]:
import random
%load_ext autoreload
%autoreload 2
from absl import logging
logging.set_verbosity(logging.INFO)

#with jax.profiler.trace(logs):
res = ode.train_ehr(subject_interface=subjects_interface,
                diag_gram=diag_gram,
                proc_gram=proc_gram,
                rng=random.Random(42),
                **config['model'],
                **config['training'],
                verbose_debug=False,
                shape_debug=False,
                nan_debug=False,
                memory_profile=False)

DEBUG:absl:Compiling prim_fun (140237611391552) for args (ShapedArray(int32[]),).
DEBUG:absl:Compiling prim_fun (140237611306304) for args (ShapedArray(int32[]), ShapedArray(int32[])).
DEBUG:absl:Compiling prim_fun (140237611346624) for args (ShapedArray(int32[]),).
DEBUG:absl:Compiling prim_fun (140237611270272) for args (ShapedArray(uint32[]),).
DEBUG:absl:Compiling <lambda> (140237611692736) for args (ShapedArray(int32[]), ShapedArray(uint32[])).
DEBUG:absl:Compiling prim_fun (140237611710016) for args (ShapedArray(uint32[1]), ShapedArray(uint32[1])).
DEBUG:absl:Compiling prim_fun (140237611616576) for args (ShapedArray(float32[]),).
DEBUG:absl:Compiling prim_fun (140237611682752) for args (ShapedArray(float32[]),).
DEBUG:absl:Compiling prim_fun (140237611305472) for args (ShapedArray(float32[]),).
DEBUG:absl:Compiling prim_fun (140237611654912) for args (ShapedArray(float32[]),).
DEBUG:absl:Compiling prim_fun (140237611616576) for args (ShapedArray(float32[]),).
DEBUG:absl:Compilin

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


DEBUG:absl:Compiling prim_fun (140237611545984) for args (ShapedArray(float32[100]), ShapedArray(float32[100])).
DEBUG:absl:Compiling prim_fun (140237611246016) for args (ShapedArray(float32[], weak_type=True),).
DEBUG:absl:Compiling _threefry_split (140237611546112) for args (ShapedArray(uint32[2]),).
DEBUG:absl:Compiling _truncated_normal (140237611501952) for args (ShapedArray(uint32[2]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True)).
DEBUG:absl:Compiling fn (140237612307584) for args (ShapedArray(float32[]), ShapedArray(float32[200,100])).
DEBUG:absl:Compiling fn (140237612382784) for args (ShapedArray(float32[200,100]), ShapedArray(float32[])).
DEBUG:absl:Compiling dot (140237612208064) for args (ShapedArray(float32[200]), ShapedArray(float32[200,100])).
DEBUG:absl:Compiling fn (140237611557056) for args (ShapedArray(float32[100]), ShapedArray(float32[100])).
DEBUG:absl:Compiling <lambda> (140237611515328) for args (ShapedArray(float32[100]),).
DE

DEBUG:absl:Compiling fn (140237613078528) for args (ShapedArray(float32[40]), ShapedArray(float32[], weak_type=True)).
DEBUG:absl:Compiling _where (140237613899712) for args (ShapedArray(bool[40]), ShapedArray(float32[40]), ShapedArray(float32[40])).
DEBUG:absl:Compiling _truncated_normal (140237615292672) for args (ShapedArray(uint32[2]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True)).
DEBUG:absl:Compiling fn (140237613080064) for args (ShapedArray(float32[]), ShapedArray(float32[40,550])).
DEBUG:absl:Compiling fn (140237612227968) for args (ShapedArray(float32[40,550]), ShapedArray(float32[])).
DEBUG:absl:Compiling dot (140237612227968) for args (ShapedArray(float32[40]), ShapedArray(float32[40,550])).
DEBUG:absl:Compiling fn (140237612227968) for args (ShapedArray(float32[550]), ShapedArray(float32[550])).
DEBUG:absl:Compiling <lambda> (140237613329280) for args (ShapedArray(float32[550]),).
DEBUG:absl:Compiling _truncated_normal (140237614288512) fo

DEBUG:absl:Compiling apply_fn (140237622855232) for args (ShapedArray(float32[150]), ShapedArray(float32[50,150]), ShapedArray(float32[50,150]), ShapedArray(float32[50]), ShapedArray(float32[650,50]), ShapedArray(float32[50]), ShapedArray(float32[550]), ShapedArray(float32[550]), ShapedArray(float32[100])).
visit #1/1084 - odeint:   0%|▎                                                                                                                                             | 1/443 [00:03<22:08,  3.01s/it]DEBUG:absl:Compiling apply_fn (140237622856704) for args (ShapedArray(float32[50]), ShapedArray(float32[120,50]), ShapedArray(float32[50]), ShapedArray(float32[120,50]), ShapedArray(float32[50]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[70]), AbstractUnit(), AbstractUnit(), AbstractUnit(), AbstractUnit(), AbstractUnit(), AbstractUnit()).
DEBUG:absl:Compiling apply_fn (140237623980736) for args (ShapedArray(float32[50]), ShapedArray(float32[120,50]), ShapedArray(flo

...

 70%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████▌                                                | 309/443 [2:24:06<1:06:07, 29.61s/it]DEBUG:absl:Compiling backward_pass (140236010304128) for args (ShapedArray(float32[]), ShapedArray(float32[122]), ShapedArray(float32[])).
DEBUG:absl:Compiling prim_fun (140235981473408) for args (ShapedArray(float32[]),).
info retrieval:  70%|████████████████████████████████████████████████████████████████████████████████████████████████████▍                                           | 309/443 [2:24:18<1:06:07, 29.61s/it]DEBUG:absl:Compiling _average (140235981399168) for args (ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[]), ShapedArray(float32[]), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float

info retrieval:  70%|████████████████████████████████████████████████████████████████████████████████████████████████████▍                                           | 309/443 [2:24:24<1:06:07, 29.61s/it]DEBUG:absl:Compiling _average (140235980234688) for args (ShapedArray(float32[]), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32

 70%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████▉                                                | 310/443 [2:24:34<1:07:43, 30.55s/it]DEBUG:absl:Compiling backward_pass (140236380668032) for args (ShapedArray(float32[]), ShapedArray(float32[44]), ShapedArray(float32[])).
DEBUG:absl:Compiling prim_fun (140236041290176) for args (ShapedArray(float32[]),).
info retrieval:  70%|████████████████████████████████████████████████████████████████████████████████████████████████████▊                                           | 310/443 [2:24:49<1:07:43, 30.55s/it]DEBUG:absl:Compiling _average (140235988614080) for args (ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArray(float32[], weak_type=True), ShapedArray(float32[]), ShapedArra

INFO:ode:
                          Training   Valdation
accuracy                  0.792694    0.793134
recall                    0.715736    0.675926
npv                       0.984077    0.986867
specificity               0.796181    0.796970
precision                 0.137293    0.098250
f1-score                  0.230392    0.171563
tp                        0.031030    0.021420
tn                        0.761664    0.771714
fp                        0.194982    0.196596
fn                        0.012324    0.010270
points_count            199.000000  153.000000
odeint_weeks_per_visit    5.084709    2.711485
nfe_per_point             0.000000    0.000000
nfe_per_week              0.000000    0.000000
nfex1000                  0.000000    0.000000
visit #82/1084:  70%|█████████████████████████████████████████████████████████████████████████████████████████████████████                                           | 311/443 [2:24:57<1:03:25, 28.83s/it]

KeyboardInterrupt: 